In [1]:
import pandas as pd
import os
import re
import json
import yaml
from glob import glob
from tqdm import tqdm
from pprint import pprint
import torch
import pytorch_lightning as pl
from rouge import Rouge # 모델의 성능을 평가하기 위한 라이브러리입니다.

from torch.utils.data import Dataset , DataLoader
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, BartForConditionalGeneration, BartConfig
from transformers import T5TokenizerFast, T5ForConditionalGeneration, T5Config
from transformers import Seq2SeqTrainingArguments, Seq2SeqTrainer
from transformers import Trainer, TrainingArguments
from transformers import EarlyStoppingCallback

import wandb # 모델 학습 과정을 손쉽게 Tracking하고, 시각화할 수 있는 라이브러리입니다.

# visualization
import matplotlib
matplotlib.rcParams['axes.unicode_minus'] = False
import matplotlib.pyplot as plt
import matplotlib.font_manager as fm
fe = fm.FontEntry(
    fname=r'/usr/share/fonts/NanumFont/NanumGothic.ttf', # ttf 파일이 저장되어 있는 경로
    name='NanumBarunGothic')                        # 이 폰트의 원하는 이름 설정
fm.fontManager.ttflist.insert(0, fe)              # Matplotlib에 폰트 추가
plt.rcParams.update({'font.size': 10, 'font.family': 'NanumBarunGothic'}) # 폰트 설정
plt.rc('font', family='NanumBarunGothic')
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')

In [2]:
# config 설정에 tokenizer 모듈이 사용되므로 미리 tokenizer를 정의해줍니다.
model_dir = "lcw99/t5-base-korean-text-summary"
tokenizer = T5TokenizerFast.from_pretrained(model_dir) 

# https://huggingface.co/paust/pko-t5-base
# transformers 의 API 를 사용하여 접근 가능합니다. 
# tokenizer 를 사용할때는 T5Tokenizer 가 아니라 T5TokenizerFast 를 사용해주십시오. 
# model 은 T5ForConditionalGeneration 를 그대로 활용하시면 됩니다.

In [3]:
config_data = {
    "general": {
        "data_path": "your_path", # 모델 생성에 필요한 데이터 경로를 사용자 환경에 맞게 지정합니다.
        "model_name": f"{model_dir}", # 불러올 모델의 이름을 사용자 환경에 맞게 지정할 수 있습니다.
        "output_dir": "./" # 모델의 최종 출력 값을 저장할 경로를 설정합니다.
    },
    "tokenizer": {
        "encoder_max_len": 1024,
        "decoder_max_len": 150,
        "bos_token": f"{tokenizer.bos_token}",
        "eos_token": f"{tokenizer.eos_token}",
        "unk_token": f"{tokenizer.unk_token}",
        "pad_token": f"{tokenizer.pad_token}",
        # 특정 단어들이 분해되어 tokenization이 수행되지 않도록 special_tokens을 지정해줍니다.
        "special_tokens": ['#Person1#', '#Person2#', '#Person3#', '#Person4#', '#Person5#', '#Person6#', '#Person7#',
                           '#DateOfBirth#', '#CarNumber#', '#Email#', '#CardNumber#', '#Address#', '#SSN#', '#PhoneNumber#', '#PassportNumber#']
    },
    "training": {
        "overwrite_output_dir": True,
        "num_train_epochs": 50,
        "learning_rate": 1e-5,
        "per_device_train_batch_size": 4, # 50
        "per_device_eval_batch_size": 16, # 32
        "warmup_ratio": 0.1,
        "weight_decay": 0.01,
        "lr_scheduler_type": 'cosine',
        "optim": 'adamw_torch',
        "gradient_accumulation_steps": 16, # 몇 개의 작은 배치를 합쳐서 큰 배치처럼 처리할지를 결정하는 파라미터: 메모리 제한 극복, 더 나은 성능
        "evaluation_strategy": 'epoch',
        "save_strategy": 'epoch',
        "save_total_limit": 7,
        "fp16": True,
        "load_best_model_at_end": True,
        "seed": 42,
        "logging_dir": "./logs",
        "logging_strategy": "epoch",
        "predict_with_generate": True,
        "generation_max_length": 150,
        "do_train": True,
        "do_eval": True,
        "early_stopping_patience": 5, # 3
        "early_stopping_threshold": 0.0001, # 0.001
        "report_to": "wandb" # (선택) wandb를 사용할 때 설정합니다.
    },
    # (선택) wandb 홈페이지에 가입하여 얻은 정보를 기반으로 작성합니다.
    "wandb": {
        "entity": "entity_name",
        "project": "project_name",
        "name": "name"
    },
    "inference": {
        "ckt_path": "model ckt path", # 사전 학습이 진행된 모델의 checkpoint를 저장할 경로를 설정합니다.
        "result_path": "./prediction/",
        "no_repeat_ngram_size": 2,
        "early_stopping": True,
        "generate_max_length": 150,
        "num_beams": 4,
        "batch_size" : 16, # 32
        # 정확한 모델 평가를 위해 제거할 불필요한 생성 토큰들을 정의합니다.
        "remove_tokens": ['<usr>', f"{tokenizer.bos_token}", f"{tokenizer.eos_token}", f"{tokenizer.unk_token}", f"{tokenizer.pad_token}"]
    }
}

In [4]:
# 모델의 구성 정보를 YAML 파일로 저장합니다.
config_path = "./config.yaml"
with open(config_path, "w") as file:
    yaml.dump(config_data, file, allow_unicode=True)

# 저장된 config 파일을 불러옵니다.
config_path = "./config.yaml"

with open(config_path, "r") as file:
    loaded_config = yaml.safe_load(file)

loaded_config['general']['data_path'] = '../../data'

In [5]:
# config에 저장된 데이터 경로를 통해 train과 validation data를 불러옵니다.
data_path = loaded_config['general']['data_path']

# train data의 구조와 내용을 확인합니다.
train_df = pd.read_csv(os.path.join(data_path,'train.csv'))
display(train_df.tail())

# dev data의 구조와 내용을 확인합니다.
dev_df = pd.read_csv(os.path.join(data_path,'dev.csv'))
display(dev_df.tail())

train_df_copy = train_df.copy()
dev_df_copy = dev_df.copy()

fname                                           dialogue  \
12452  train_12455  #Person1#: 실례합니다. 맨체스터 출신의 그린 씨이신가요?\n#Person2...   
12453  train_12456  #Person1#: 이윙 씨가 우리가 컨퍼런스 센터에 오후 4시에 도착해야 한다고 ...   
12454  train_12457  #Person1#: 오늘 어떻게 도와드릴까요?\n#Person2#: 차를 빌리고 싶...   
12455  train_12458  #Person1#: 오늘 좀 행복해 보이지 않아. 무슨 일 있어?\n#Person2...   
12456  train_12459  #Person1#: 엄마, 다음 토요일에 이 삼촌네 가족을 방문하기 위해 비행기를 ...   

                                                 summary     topic  
12452  탄 링은 흰머리와 수염으로 쉽게 인식되는 그린 씨를 만나 호텔로 데려갈 예정입니다....  누군가를 태우다  
12453  #Person1#과 #Person2#는 이윙 씨가 늦지 않도록 요청했기 때문에 컨퍼...   컨퍼런스 센터  
12454       #Person2#는 #Person1#의 도움으로 5일 동안 소형 차를 빌립니다.      차 렌트  
12455  #Person2#의 엄마가 일자리를 잃었다. #Person2#는 엄마가 우울해하지 ...        실직  
12456  #Person1#은 다음 토요일에 이 삼촌네를 방문할 때 가방을 어떻게 싸야 할지 ...      짐 싸기

fname                                           dialogue  \
494  dev_495  #Person1#: 이제 새해가 되어서 새로운 시작을 하려고 결심했어. \r\n#P...   
495  dev_496  #Person1#: 너, 조랑 결혼했지? \r\n#Person2#: 조? 무슨 말인...   
496  dev_497  #Person1#: 무엇을 도와드릴까요, 부인?\r\n#Person2#: 몇 주 동...   
497  dev_498  #Person1#: 안녕하세요, 아마존 고객 서비스입니다. 무엇을 도와드릴까요?\n...   
498  dev_499  #Person1#: 여름이 다 되어간다는 게 믿기지 않아.\r\n#Person2#:...   

                                               summary    topic  
494  #Person1#은 새해에 금연을 하고 커밍아웃하기로 결정했습니다. #Person2...       새해  
495  #Person1#은 #Person2#가 조와 결혼했다고 생각했다. #Person2#...  사랑에 빠지다  
496  #Person2#의 차에서 이상한 소리가 납니다. #Person1#는 브레이크를 교...       소음  
497  #Person2#님이 아마존 고객 서비스에 전화하여 아마존에서 받은 책에 한 페이지...   빠진 페이지  
498  #Person2#는 #Person1#에게 여름 휴가 동안 파티를 도와주는 회사에서 ...    여름 휴가

# 대화문에 개행문자 적용 잘 되어있는지 확인

In [6]:
train_dialogue_n = train_df_copy['dialogue'].apply(lambda x: x.count('\n'))
train_dialogue_n.describe()

count    12457.000000
mean         8.490728
std          4.150287
min          1.000000
25%          6.000000
50%          8.000000
75%         11.000000
max         60.000000
Name: dialogue, dtype: float64

In [7]:
n_1_list = train_dialogue_n[train_dialogue_n <= 1].reset_index()['index'].tolist()
for idx in n_1_list:
    print(f'\n[{idx}]')
    print('-----'*20)
    print(train_df_copy.iloc[idx, 1])
    print('-----'*20)


[32]
----------------------------------------------------------------------------------------------------
#Person1#: 제가 많이 들어본 곳은 로스앤젤레스에요. 기후가 꽤 좋아요. 일년 내내 꽃이 피고, 일년 내내 수영을 할 수 있어요. 어떻게 생각하세요?
#Person2#: 음, 해변은 아름다워요. 하지만 그곳 사람들은 더러운 공기에 대해 매우 짜증을 내고 있어요. 즉, 안개, 연기, 자동차 배기가스의 조합 말이죠. 그것을 날려버릴 바람이 충분하지 않아요.
----------------------------------------------------------------------------------------------------

[77]
----------------------------------------------------------------------------------------------------
#Person1#: 신생아 때문에 밤새도록 잠을 못 자겠네요.
#Person2#: 제 어머니가 들어오신 이후로 아기가 꽤 잘 있어요, 그리고 밤에 더 오래 잠을 자고 있어요. 밤에 잠을 못 자게 하는 건 어머니로서의 제 생각들이에요.
----------------------------------------------------------------------------------------------------

[129]
----------------------------------------------------------------------------------------------------
#Person1#: 신고하고 싶은 일이 있습니다, 선생님. 제가 테이블에서 웨이터가 나타날 때까지 십 분을 기다렸고, 결국 서빙을 받았습니다. 그런데 제가 주문한 것이 아니더군요.
#Person2#: 정말 죄송합니다, 부인. 오늘은 평소보다 조금 더 바쁜

# special token을 통해 적절하지 않은 형식 찾기

> 데이터 전처리에서 얻은 special token

{'#Person3#', '#PhoneNumber#', '#Person5#', '#PassportNumber#', '#DateOfBirth#', '#Address#', '#Person6#', '#CarNumber#', '#SSN#', '#Person7#', '#CardNumber#', '#Person4#', '#Person2#', '#Person#', '#Email#', '#Person1#'}

In [8]:
def findall_pattern(df, pattern):
    idx_list = []
    for idx in range(0, df.shape[0]):
        text = df.loc[idx, 'dialogue']
        pattern = pattern
        masked = re.findall(pattern, text)
        if len(masked) > 0:
            idx_list.append(idx)
    return idx_list, masked

def fullmatch_pattern(df, pattern):
    idx_list = []
    for idx in range(0, df.shape[0]):
        text = df.loc[idx, 'dialogue']
        pattern = pattern
        masked = re.fullmatch(pattern, text)
        if len(masked) > 0:
            idx_list.append(idx)
    return idx_list, masked

# Train

## 화자 관련

In [9]:
train_df_person = train_df.copy()
del_token = ['#PhoneNumber#', '#PassportNumber#', '#DateOfBirth#', '#Address#', '#CarNumber#', '#SSN#', '#CardNumber#', '#Email#']
pattern = '|'.join(re.escape(token) for token in del_token)
for idx in tqdm(range(0, train_df_copy.shape[0])):
    text = train_df_copy.iloc[idx, 1]
    text2 = re.sub(pattern, '', text)
    train_df_person.iloc[idx, 1] = text2

100%|██████████| 12457/12457 [00:00<00:00, 20851.22it/s]


In [10]:
print(train_df_person.iloc[12428, 1])

#Person1#: 맹세코, 제 다리가 부러진 것 같아요.
#Person2#: 여기, 선생님, 이 휠체어에 앉으세요.
#Person1#: 감사합니다.
#Person2#: 의사 선생님이 곧 오실 거예요. 몇 가지 질문을 드려야 해요.
#Person1#: 알겠습니다.
#Person2#: 이름, 나이, 생년월일을 알려주시겠어요?
#Person1#: 존 테일러, 32살, 입니다.
#Person2#: 건강 보험 회사와 보험 번호는요?
#Person1#: 그게 없어요.
#Person2#: 뭐라고요?
#Person1#: 건강 보험을 가지고 있지 않아요.
#Person2#: 이런, 테일러씨, 이 부러진 다리 치료비가 상당히 비싸질 거예요.
#Person1#: 오마이갓!


### Person이 아니라 한국어인 경우

In [11]:
idx_list, _ = findall_pattern(train_df_person, r'#[가-힣]+')
for idx in idx_list:
    print(f'\n[{idx}]')
    print('----'*20)
    print(train_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list), idx_list)


[839]
--------------------------------------------------------------------------------
#Person1#: 안녕하세요, 저희 은행에 오신 것을 환영합니다. 오늘은 무엇을 도와드릴까요?
#Person2#: 정기예금에 대해 조언이 필요합니다.
#Person1#: 무슨 문제가 있으신가요?
#Person2#: 아니요, 문제 없습니다. 그냥 정기예금 중 하나가 만기가 되어서 어떻게 처리해야 할지 잘 모르겠어요.
#Person1#: 그렇군요. 두 가지 선택이 있는데, 갱신하거나 교환할 수 있습니다. 어느 쪽을 선호하시나요?
#Person2#: 음.. 지금까지 서비스에 만족하고 있으니 갱신하고 싶어요.
#Person1#: 문제없습니다. 하지만 만기 시 계정 갱신이라는 새로운 서비스가 도입되었음을 알려드려도 될까요?
#Person2#: 네. . .
#사람1만기 시 계정 갱신 서비스는 만기일이 다가오면 자동으로 갱신되며, 고객님이 직접 이곳에 오셔서 정리하실 필요가 없다는 뜻입니다. 여기에 서명만 하시면 저희가 모든 것을 설정해 드립니다.
#Person2#: 그게 저한테 딱 맞아요. 저는 센터에서 꽤 멀리 떨어져 살고 있어서 센터에 가는 것이 번거로울 때가 있거든요.
--------------------------------------------------------------------------------

[1213]
--------------------------------------------------------------------------------
#Person1#: 화성에 관한 흥미로운 보고서를 읽고 있어요.
#Person2#: 뭐라고 적혀있나요? 화성 표면 아래에 물이 여전히 존재할 수 있다는 내용인가요?
#Person1#: 물론이죠! 화성 표면 아래에 물이 묻혀있다고 하네요. 얼마나 깊냐의 문제일 뿐이죠.
#Person2#: 그럼 화성의 토양이 간단한 식물을 키울 수 있을 만큼 비옥할

### 영어와 한국어이면서, 마지막이 숫자가 없거나 #으로 안 끝나는 경우

In [12]:
idx_list2, _ = findall_pattern(train_df_person, r'#\b[A-Za-z가-힣]+\b')
for idx in idx_list2:
    print(f'\n[{idx}]')
    print('----'*20)
    print(train_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list2), idx_list2)


[420]
--------------------------------------------------------------------------------
#Person1#: 안녕하세요. ABC 수입사입니다. 도와드릴 일이 있으신가요?
#Person2#: 네, 제임스 존슨 씨와 통화할 수 있을까요?
#Person1#: 죄송하지만 존슨 씨는 지금 연락이 불가능합니다. 메시지를 남기시겠습니까?
#Person2#: 저는 스타 전자의 리처드 알렉산더입니다. 오늘 오후에 꼭 전화를 돌려주셔야 합니다.
#Person1#: 그분이 귀하의 사무실 번호와 휴대폰 번호를 가지고 계신가요?
#Person2#: 그런 것 같은데, 다시 한 번 알려드리겠습니다.
#Person1#: 알겠습니다.
#Person2#: 제 사무실 번호는 #PhoneNumber이고, 휴대폰 번호는 입니다. 오늘 하루 종일 휴대폰으로 언제든지 연락하실 수 있고, 사무실 번호로는 오후 6시 이전에 연락하실 수 있습니다.
#Person1#: 알겠습니다, 그분이 사무실로 돌아오는 대로 메시지를 전달하겠습니다.
--------------------------------------------------------------------------------

[1213]
--------------------------------------------------------------------------------
#Person1#: 화성에 관한 흥미로운 보고서를 읽고 있어요.
#Person2#: 뭐라고 적혀있나요? 화성 표면 아래에 물이 여전히 존재할 수 있다는 내용인가요?
#Person1#: 물론이죠! 화성 표면 아래에 물이 묻혀있다고 하네요. 얼마나 깊냐의 문제일 뿐이죠.
#Person2#: 그럼 화성의 토양이 간단한 식물을 키울 수 있을 만큼 비옥할 수 있을까요?
#Person1#: 토양은 무엇이든 자라게 하려면 상당한 양의 비료가 필요할 것입니다. 그리고 자외선으로부터 보호받아야 하겠죠.
#Person2#: 사실

### 첫시작에 #이 없는 경우

In [13]:
idx_list3, _ = findall_pattern(train_df_person, r'(?<!#)\b[A-Za-z가-힣0-9]+\b#')
for idx in idx_list3:
    print(f'\n[{idx}]')
    print('----'*20)
    print(train_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list3))


[1125]
--------------------------------------------------------------------------------
사람1#: 제니, 이번 금요일에, 음... 바쁘세요?
#Person2#: 네, 금요일에는 일 끝나고 바로 수업이 있어요.
#Person1#: 그렇군요. 그럼 토요일은 어때요? 그날 시간 있으세요?
#Person2#: 토요일에는 부모님이 오시려고 해요. 왜요?
#Person1#: 그럼 오늘은요? 오늘은 다른 계획이 있으세요?
#Person2#: 아니요. 뭔가 하려고 했어요?
#Person1#: 네! 네! 저녁에 식사 대접하려고 했어요.
#Person2#: 오! 좋아요! 여섯 시에 어떠세요?
--------------------------------------------------------------------------------

[1142]
--------------------------------------------------------------------------------
사람1#: 실례합니다. 저는 STM에서 왔어요. 우리 도시의 교통에 대한 설문 조사를 하고 있는데, 몇 가지 질문해도 괜찮을까요?
#Person2#: 아니요, 괜찮아요. 계속하세요.
#Person1#: 좋아요, 감사합니다. 무슨 일을 하세요?
#Person2#: 저는 선생님입니다. 아이들에게 프랑스어를 가르쳐요.
#Person1#: 좋네요. 학교에서 멀리 사세요? 일반적으로 출근은 어떻게 하시나요?
#Person2#: 대부분 차를 타고 가요. 가끔은 자전거를 타기도 해요. 제 집은 학교에서 꽤 멀어요, 약 20마일이나 되요. 그래서 학교에 가려면 한 시간 정도 걸려요. 하지만 차를 타면 교통이 막히지 않는다면 15분도 안 걸려요.
#Person1#: 알겠습니다. 자주 교통 체증이 있나요?
#Person2#: 네, 그렇죠! 자주 교통 체증에 걸려요, 문제가 점점 심해져요.
#Person1#: 제 질문은 여기까지입니다. 감사

### 양쪽에 #이 없는 경우

In [14]:
idx_list4, _ = findall_pattern(train_df_person, r'(?<!#)\b사람[0-9]+:\s\b') # 사람 Person
for idx in idx_list4:
    print(f'\n[{idx}]')
    print('----'*20)
    print(train_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list4))

0


### 4가지 경우의 인덱스 값들 중복 제거

In [15]:
person_idx = list(set(idx_list + idx_list2 + idx_list3 + idx_list4))
person_idx = sorted(person_idx)
print(len(person_idx), person_idx)

24 [420, 839, 1125, 1142, 1213, 1236, 1250, 1266, 1278, 1281, 1283, 1301, 1302, 1306, 1322, 1547, 1609, 1899, 4537, 8318, 8722, 9750, 9779, 10370]


In [16]:
for idx in person_idx:
    print(f'\n[{idx}]')
    print('----'*20)
    print(train_df_copy.iloc[idx, 1])
    print('----'*20)


[420]
--------------------------------------------------------------------------------
#Person1#: 안녕하세요. ABC 수입사입니다. 도와드릴 일이 있으신가요?
#Person2#: 네, 제임스 존슨 씨와 통화할 수 있을까요?
#Person1#: 죄송하지만 존슨 씨는 지금 연락이 불가능합니다. 메시지를 남기시겠습니까?
#Person2#: 저는 스타 전자의 리처드 알렉산더입니다. 오늘 오후에 꼭 전화를 돌려주셔야 합니다.
#Person1#: 그분이 귀하의 사무실 번호와 휴대폰 번호를 가지고 계신가요?
#Person2#: 그런 것 같은데, 다시 한 번 알려드리겠습니다.
#Person1#: 알겠습니다.
#Person2#: 제 사무실 번호는 #PhoneNumber이고, 휴대폰 번호는 #PhoneNumber#입니다. 오늘 하루 종일 휴대폰으로 언제든지 연락하실 수 있고, 사무실 번호로는 오후 6시 이전에 연락하실 수 있습니다.
#Person1#: 알겠습니다, 그분이 사무실로 돌아오는 대로 메시지를 전달하겠습니다.
--------------------------------------------------------------------------------

[839]
--------------------------------------------------------------------------------
#Person1#: 안녕하세요, 저희 은행에 오신 것을 환영합니다. 오늘은 무엇을 도와드릴까요?
#Person2#: 정기예금에 대해 조언이 필요합니다.
#Person1#: 무슨 문제가 있으신가요?
#Person2#: 아니요, 문제 없습니다. 그냥 정기예금 중 하나가 만기가 되어서 어떻게 처리해야 할지 잘 모르겠어요.
#Person1#: 그렇군요. 두 가지 선택이 있는데, 갱신하거나 교환할 수 있습니다. 어느 쪽을 선호하시나요?
#Person2#: 음.. 지금까지 서비스에 만족하고 있으니 갱

In [17]:
print(
    re.sub(r'#PhoneNumber[가-힣]', '#PhoneNumber#', train_df_copy.iloc[420, 1])
)

#Person1#: 안녕하세요. ABC 수입사입니다. 도와드릴 일이 있으신가요?
#Person2#: 네, 제임스 존슨 씨와 통화할 수 있을까요?
#Person1#: 죄송하지만 존슨 씨는 지금 연락이 불가능합니다. 메시지를 남기시겠습니까?
#Person2#: 저는 스타 전자의 리처드 알렉산더입니다. 오늘 오후에 꼭 전화를 돌려주셔야 합니다.
#Person1#: 그분이 귀하의 사무실 번호와 휴대폰 번호를 가지고 계신가요?
#Person2#: 그런 것 같은데, 다시 한 번 알려드리겠습니다.
#Person1#: 알겠습니다.
#Person2#: 제 사무실 번호는 #PhoneNumber#고, 휴대폰 번호는 #PhoneNumber#입니다. 오늘 하루 종일 휴대폰으로 언제든지 연락하실 수 있고, 사무실 번호로는 오후 6시 이전에 연락하실 수 있습니다.
#Person1#: 알겠습니다, 그분이 사무실로 돌아오는 대로 메시지를 전달하겠습니다.


In [18]:
train_df_copy.iloc[420, 1] = re.sub(r'#PhoneNumber[가-힣]', '#PhoneNumber#', train_df_copy.iloc[420, 1])
train_df_copy.iloc[839, 1] = re.sub(r'#사람1', '#Person1#: ', train_df_copy.iloc[839, 1])
train_df_copy.iloc[1125, 1] = re.sub(r'사람1#', '#Person1#', train_df_copy.iloc[1125, 1])

train_df_copy.iloc[1142, 1] = re.sub(r'사람1#', '#Person1#', train_df_copy.iloc[1142, 1])
train_df_copy.iloc[1213, 1] = re.sub(r'#하지만', '#Person1#:', train_df_copy.iloc[1213, 1])
train_df_copy.iloc[1236, 1] = re.sub(r'#고객님', '#Person2#: 고객님', train_df_copy.iloc[1236, 1])

train_df_copy.iloc[1250, 1] = re.sub(r'#여기', '#Person1#: 여기', train_df_copy.iloc[1250, 1])
train_df_copy.iloc[1266, 1] = re.sub(r'#고객님', '#Person2#: 고객님', train_df_copy.iloc[1266, 1])
train_df_copy.iloc[1278, 1] = re.sub(r'#고객님', '#Person2#: 고객님', train_df_copy.iloc[1278, 1])

train_df_copy.iloc[1281, 1] = re.sub(r'#잠깐만요', '#Person1#: 잠깐만요', train_df_copy.iloc[1281, 1])
train_df_copy.iloc[1283, 1] = re.sub(r'#어디', '#Person1#: 어디', train_df_copy.iloc[1283, 1])
train_df_copy.iloc[1301, 1] = re.sub(r'#샐러드용', '#Person1#: 샐러드용', train_df_copy.iloc[1301, 1])

train_df_copy.iloc[1302, 1] = re.sub(r'#페리에와', '#Person1#: 페리에와', train_df_copy.iloc[1302, 1])
train_df_copy.iloc[1306, 1] = re.sub(r'#나', '#Person2#: 나', train_df_copy.iloc[1306, 1])
train_df_copy.iloc[1322, 1] = re.sub(r'#여기서', '#Person1#: 여기서', train_df_copy.iloc[1322, 1])

train_df_copy.iloc[1547, 1] = re.sub(r'#작은', '#Person2#: 작은', train_df_copy.iloc[1547, 1])
train_df_copy.iloc[1609, 1] = re.sub(r'#여기', '#Person2#: 여기', train_df_copy.iloc[1609, 1])
train_df_copy.iloc[1899, 1] = re.sub(r'#Person#', '#Person2#', train_df_copy.iloc[1899, 1])

train_df_copy.iloc[4537, 1] = re.sub(r'#Person\s', '#Person', train_df_copy.iloc[4537, 1])
train_df_copy.iloc[9750, 1] = re.sub(r'(?<!#)Person', '#Person', train_df_copy.iloc[9750, 1])
train_df_copy.iloc[9779, 1] = re.sub(r'(?<!#)Person', '#Person', train_df_copy.iloc[9779, 1])

In [19]:
train_df_person.iloc[420, 1] = re.sub(r'#PhoneNumber[가-힣]', '#PhoneNumber#', train_df_person.iloc[420, 1])
train_df_person.iloc[839, 1] = re.sub(r'#사람1', '#Person1#: ', train_df_person.iloc[839, 1])
train_df_person.iloc[1125, 1] = re.sub(r'사람1#', '#Person1#', train_df_person.iloc[1125, 1])

train_df_person.iloc[1142, 1] = re.sub(r'사람1#', '#Person1#', train_df_person.iloc[1142, 1])
train_df_person.iloc[1213, 1] = re.sub(r'#하지만', '#Person1#:', train_df_person.iloc[1213, 1])
train_df_person.iloc[1236, 1] = re.sub(r'#고객님', '#Person2#: 고객님', train_df_person.iloc[1236, 1])

train_df_person.iloc[1250, 1] = re.sub(r'#여기', '#Person1#: 여기', train_df_person.iloc[1250, 1])
train_df_person.iloc[1266, 1] = re.sub(r'#고객님', '#Person2#: 고객님', train_df_person.iloc[1266, 1])
train_df_person.iloc[1278, 1] = re.sub(r'#고객님', '#Person2#: 고객님', train_df_person.iloc[1278, 1])

train_df_person.iloc[1281, 1] = re.sub(r'#잠깐만요', '#Person1#: 잠깐만요', train_df_person.iloc[1281, 1])
train_df_person.iloc[1283, 1] = re.sub(r'#어디', '#Person1#: 어디', train_df_person.iloc[1283, 1])
train_df_person.iloc[1301, 1] = re.sub(r'#샐러드용', '#Person1#: 샐러드용', train_df_person.iloc[1301, 1])

train_df_person.iloc[1302, 1] = re.sub(r'#페리에와', '#Person1#: 페리에와', train_df_person.iloc[1302, 1])
train_df_person.iloc[1306, 1] = re.sub(r'#나', '#Person2#: 나', train_df_person.iloc[1306, 1])
train_df_person.iloc[1322, 1] = re.sub(r'#여기서', '#Person1#: 여기서', train_df_person.iloc[1322, 1])

train_df_person.iloc[1547, 1] = re.sub(r'#작은', '#Person2#: 작은', train_df_person.iloc[1547, 1])
train_df_person.iloc[1609, 1] = re.sub(r'#여기', '#Person2#: 여기', train_df_person.iloc[1609, 1])
train_df_person.iloc[1899, 1] = re.sub(r'#Person#', '#Person2#', train_df_person.iloc[1899, 1])

train_df_person.iloc[4537, 1] = re.sub(r'#Person\s', '#Person', train_df_person.iloc[4537, 1])
train_df_person.iloc[9750, 1] = re.sub(r'(?<!#)Person', '#Person', train_df_person.iloc[9750, 1])
train_df_person.iloc[9779, 1] = re.sub(r'(?<!#)Person', '#Person', train_df_person.iloc[9779, 1])

idx_list, _ = findall_pattern(train_df_person, r'#[가-힣]+')
idx_list2, _ = findall_pattern(train_df_person, r'#\b[A-Za-z가-힣]+\b')
idx_list3, _ = findall_pattern(train_df_person, r'(?<!#)\b[A-Za-z가-힣0-9]+\b#')
idx_list4, _ = findall_pattern(train_df_person, r'(?<!#)\b사람[0-9]+:\s\b') # 사람 Person

person_idx = list(set(idx_list + idx_list2 + idx_list3 + idx_list4))
person_idx = sorted(person_idx)
print(len(person_idx), person_idx)

4 [420, 8318, 8722, 10370]


### 화자가 연속되는 경우

In [20]:
def reg_masking(pattern, text):
    masked = re.findall(pattern, text)
    return masked

In [21]:
masked_train = train_df_copy['dialogue'].apply(lambda x: str(reg_masking(r'#\bPerson[0-9]+\b#', x)))
for idx in range(0, train_df_copy.shape[0]):
    print(masked_train[idx])

['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#P

In [22]:
def repeat_person(word_list):
    for i in range(len(word_list) - 1):
        if word_list[i] == word_list[i+1]:
            return True
    return False

In [23]:
masked_train = masked_train.reset_index()
train_df_repeat = masked_train['dialogue'].apply(lambda x: x.lstrip('[').rstrip(']').replace("', '", ' ').strip("'").split())

In [24]:
idx_repeat = []
for idx in range(0, train_df_copy.shape[0]):
    if repeat_person(train_df_repeat[idx]) == True:
        idx_repeat.append(idx)
print(len(idx_repeat), idx_repeat)

22 [345, 484, 756, 872, 925, 982, 1033, 1220, 1294, 1419, 1424, 1440, 1475, 1497, 1791, 3628, 5441, 6759, 6799, 8645, 9898, 11578]


In [25]:
for idx in idx_repeat:
    print(f'\n[{idx}]')
    print('-----'*20)
    print(train_df_copy.iloc[idx, 1])
    # print(f'>>> {train_df_copy.iloc[idx, 2]}')
    print('-----'*20)


[345]
----------------------------------------------------------------------------------------------------
#Person1#: 의사 선생님, 제 아기를 구해주세요
#Person2#: 어떤 증상이 있나요?
#Person1#: 하루 동안 열이 있었어요. 방금 집에서 발열성 경련이 있었는데, 이빨과 주먹을 꽉 물고 눈을 뒤집었어요. 우리는 어떻게 해야 할지 몰랐어요. 구급차를 불러서 아기를 여기로 데려왔어요.
#Person2#: 경련이 얼마나 오래 지속되었나요?
#Person1#: 대략 3분 정도요.
#Person2#: 다른 불편한 점이 있나요?
#Person1#: 3일 전에 기침, 재채기, 콧물이 시작되었어요. 어제부터는 열이 나기 시작했어요.
#Person2#: 체온을 재보셨나요?
#Person1#: 오늘 아침에는 38도였고, 방금은 39도였어요.
#Person2#: 발진이 있는지 살펴보겠습니다. 발진은 없습니다.
#Person1#: 심각한가요? 수막염인가요?
#Person2#: 아니요, 수막염은 아닙니다. 단지 고열과 경련이 있는데, 이는 바이러스 상기도 감염 때문입니다.
#Person1#: 병원에 입원해야 하나요?
#Person1#: 아니요. 입원할 필요는 없습니다. 먼저 아기에게 진통제 코 드롭을 주어 체온을 내리겠습니다. 그런 다음 처방전을 드리겠습니다. 분홍색 정제는 열을 낮추는 데 사용됩니다. 체온이 38도 이상일 때 한 알을 주세요. 다른 정제는 경련을 위한 진정제입니다. 흰색 액체는 감기를 위한 것입니다. 아기에게 충분한 물을 마시게 해주세요.
#Person1#: 정말 감사합니다, 의사 선생님.
----------------------------------------------------------------------------------------------------

[484]
--------------------------------------------

In [26]:
temp = re.sub(r'않았어요.\r\n#Person1#: ', r'않았어요. ', train_df_copy.iloc[11578, 1])
# temp = re.sub(r'\n#Person1#: 컴퓨터', ' 컴퓨터', temp)
# temp = re.sub(r'#Person2#: 그래', '#Person1#: 그래', temp)
# temp = re.sub(r'#Person1#: 지금', '#Person2#: 지금', temp)
# temp = re.sub(r'#Person2#: 좋아', '#Person1#: 좋아', temp)

print(temp)

#Person1#: 쿠퍼씨! 어제 수업에서 가르쳐주신 것을 바탕으로 제 스스로 색을 만들어 보려고 했습니다. 그런데 쉽지 않았어요. 여기 보시겠어요? 보라색을 만들고 싶었는데, 파란색을 충분히 사용하지 않아서 약간 회색이고 지루하게 나왔어요.
#Person2#: 그래도 잘 만들어진 것 같아요! 이게 바로 그림 그리는 재미 중 하나죠 - 조금의 상상력으로 할 수 있는 것을 발견하고, 위험을 감수하고, 새로운 것을 시도하는 것.
#Person1#: 격려해주셔서 감사합니다.
#Person2#: 때때로 가장 아름다운 것들은 예술적인 우연에서 나옵니다. 그리고 저는 거의 모든 흥미로운 것들도 마찬가지라고 생각해요.


In [27]:
train_df_copy.iloc[345, 1] = re.sub(r'#Person1#: 아니요.', '#Person2#: 아니요.', train_df_copy.iloc[345, 1])
train_df_copy.iloc[484, 1] = re.sub(r'인상적이네.\s', '인상적이네. \n#Person2#: ', train_df_copy.iloc[484, 1])
train_df_copy.iloc[756, 1] = re.sub(r'#Person1#: 오, 안녕, 피비!\n#Person2#:\s', '#Person2#: 오, 안녕, 피비! ', train_df_copy.iloc[756, 1])

train_df_copy.iloc[872, 1] = re.sub(r'#Person1#: 중국은행', '#Person2#: 중국은행', train_df_copy.iloc[872, 1])

temp = re.sub(r'#Person1#: 적자생존', '#Person2#: 적자생존', train_df_copy.iloc[925, 1])
train_df_copy.iloc[925, 1] = re.sub(r'#Person2#: 맞아요', r'#Person1#: 맞아요', temp)

train_df_copy.iloc[982, 1] = re.sub(r'일이죠\?\n#Person2#:\s', '일이죠? ', train_df_copy.iloc[982, 1])

temp = re.sub(r'#Person2#: 아마도', '#Person1#: 아마도', train_df_copy.iloc[1033, 1])
temp = re.sub(r'#Person1#:\s\s', '#Person2#: ', temp)
temp = re.sub(r'#Person2#: 그래', '#Person1#: 그래', temp)
temp = re.sub(r'#Person1#: 지금', '#Person2#: 지금', temp)
train_df_copy.iloc[1033, 1] = re.sub(r'#Person2#: 좋아', '#Person1#: 좋아', temp)

train_df_copy.iloc[1220, 1] = re.sub(r'#Person2#: 음', '#Person1#: 음', train_df_copy.iloc[1220, 1])
train_df_copy.iloc[1294, 1] = re.sub(r'#Person1#: 네,', '#Person2#: 네,', train_df_copy.iloc[1294, 1])

train_df_copy.iloc[1419, 1] = re.sub(r'\n#Person1#: 어떠세요\?', ' 어떠세요?', train_df_copy.iloc[1419, 1])
train_df_copy.iloc[1424, 1] = re.sub(r'\s방으로', '#Person1#: 방으로', train_df_copy.iloc[1424, 1])
train_df_copy.iloc[1440, 1] = re.sub(r'\s언제 예약하시겠습니까\?', '\n#Person1#: 언제 예약하시겠습니까?', train_df_copy.iloc[1440, 1])

temp = re.sub(r'#Person2#: 그거', '#Person1#: 그거', train_df_copy.iloc[1475, 1])
train_df_copy.iloc[1475, 1] = re.sub(r'\n#Person1#: 컴퓨터', ' 컴퓨터', temp)

train_df_copy.iloc[1497, 1] = re.sub(r'\n\s복사', '\n#Person1#: 복사', train_df_copy.iloc[1497, 1])
train_df_copy.iloc[1791, 1] = re.sub(r'#Person1#: 봐', '#Person2#: 봐', train_df_copy.iloc[1791, 1])

train_df_copy.iloc[3628, 1] = re.sub(r'아니라고요. 당신의', '아니라고요.\n#Person1#: 당신의', train_df_copy.iloc[3628, 1])

repl_text = '#Person1#: 안녕, 내가 왔어! 음. . . 너의 머리가 꽤 손상되었고, 끝이 갈라져있어.\n#Person2#: 정말? 어떻게 해야 할까?\n#Person1#: 잘라내면 갈라진 끝은 해결될 거야, 하지만 딥 컨디셔닝 트리트먼트가 필요할 수도 있어.\n#Person2#: 음, 알겠어. 네가 도움이 될 것 같다고 생각하는 대로 해줘.\n#Person1#: 얼굴을 감싸는 레이어도 추가할 거야.\n#Person2#: 위쪽으로 가위로 손을 좀 봐줄 수 있을까? 내 머리 숫이 정말 많아.\n#Person1#: 문제 없어!'
train_df_copy.iloc[5441, 1] = repl_text

train_df_copy.iloc[6759, 1] = re.sub(r'\n#Person2#: 아', '아', train_df_copy.iloc[6759, 1])

train_df_copy.iloc[6799, 1] = re.sub(r'#Person1#: 그,', '#Person2#: 그,', train_df_copy.iloc[6799, 1])
train_df_copy.iloc[8645, 1] = re.sub(r'#Person2#: 저는 서프라이즈', '#Person1#: 저는 서프라이즈', train_df_copy.iloc[8645, 1])
train_df_copy.iloc[9898, 1] = re.sub(r'#Person1#: 오', '#Person2#: 오', train_df_copy.iloc[9898, 1])

train_df_copy.iloc[11578, 1] = re.sub(r'않았어요.\r\n#Person1#: ', r'않았어요. ', train_df_copy.iloc[11578, 1])

In [28]:
masked_train = train_df_copy['dialogue'].apply(lambda x: str(reg_masking(r'#\bPerson[0-9]+\b#', x)))
for idx in range(0, train_df_copy.shape[0]):
    print(masked_train[idx])

['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#P

In [29]:
masked_train = masked_train.reset_index()
train_df_repeat = masked_train['dialogue'].apply(lambda x: x.lstrip('[').rstrip(']').replace("', '", ' ').strip("'").split())

In [30]:
idx_repeat = []
for idx in range(0, train_df_copy.shape[0]):
    if repeat_person(train_df_repeat[idx]) == True:
        idx_repeat.append(idx)
print(len(idx_repeat), idx_repeat)

0 []


# Valid

## 화자 관련

In [31]:
dev_df_person = dev_df.copy()
del_token = ['#PhoneNumber#', '#PassportNumber#', '#DateOfBirth#', '#Address#', '#CarNumber#', '#SSN#', '#CardNumber#', '#Email#']
pattern = '|'.join(re.escape(token) for token in del_token)
for idx in tqdm(range(0, dev_df_copy.shape[0])):
    text = dev_df_copy.iloc[idx, 1]
    text2 = re.sub(pattern, '', text)
    dev_df_person.iloc[idx, 1] = text2

100%|██████████| 499/499 [00:00<00:00, 16084.21it/s]


### Person이 아니라 한국어인 경우

In [32]:
idx_list, _ = findall_pattern(dev_df_person, r'#[가-힣]+')
for idx in idx_list:
    print(f'\n[{idx}]')
    print('----'*20)
    print(dev_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list), idx_list)


[48]
--------------------------------------------------------------------------------
#Person1#: 무엇을 도와드릴까요?
#Person2#: 네, 다음 주 일요일 전에 출발하는 캐나다 캘거리행 항공편의 좌석 3석을 예약하고 싶습니다.
#Person1#: 이코노미 클래스인가요?
#Person2#: 네.
#Person1#: 편도인가요, 왕복인가요?
#Person2#: 편도입니다.
#Person1#: 직항편이 없습니다. 밴쿠버에서 환승하셔야 합니다.
#Person2#: 괜찮아요.
#다음 주 금요일 오전 10시에 베이징에서 출발하는 캐나다항공 30편이 있습니다. 좌석이 3개 있습니다. 괜찮을까요?
#Person2#: 네, 괜찮습니다.
#Person1#: 성함을 말씀해 주세요.
#Person2#: 바질, 바질입니다. 티켓이 얼마인가요?
#Person1#: 한 장당 580달러입니다.
--------------------------------------------------------------------------------
1 [48]


### 영어와 한국어이면서, 마지막이 숫자가 없거나 #으로 안 끝나는 경우

In [33]:
idx_list2, _ = findall_pattern(dev_df_person, r'#\b[A-Za-z가-힣]+\b')
for idx in idx_list2:
    print(f'\n[{idx}]')
    print('----'*20)
    print(dev_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list2), idx_list2)


[48]
--------------------------------------------------------------------------------
#Person1#: 무엇을 도와드릴까요?
#Person2#: 네, 다음 주 일요일 전에 출발하는 캐나다 캘거리행 항공편의 좌석 3석을 예약하고 싶습니다.
#Person1#: 이코노미 클래스인가요?
#Person2#: 네.
#Person1#: 편도인가요, 왕복인가요?
#Person2#: 편도입니다.
#Person1#: 직항편이 없습니다. 밴쿠버에서 환승하셔야 합니다.
#Person2#: 괜찮아요.
#다음 주 금요일 오전 10시에 베이징에서 출발하는 캐나다항공 30편이 있습니다. 좌석이 3개 있습니다. 괜찮을까요?
#Person2#: 네, 괜찮습니다.
#Person1#: 성함을 말씀해 주세요.
#Person2#: 바질, 바질입니다. 티켓이 얼마인가요?
#Person1#: 한 장당 580달러입니다.
--------------------------------------------------------------------------------

[63]
--------------------------------------------------------------------------------
#Person1#: 좋아요, 이제 초기 입금에 대해 계속 이야기해 보겠습니다.
#Person2#: 좋은 생각입니다. 얼마를 예치해야 하나요?
#Person1#: 계약 저축의 경우 100, 000위안이 필요합니다.
#Person2#: 필요한 경우 인출은 어떻게 하나요?
#Person1#: 계약 저축 계좌는 결제 계좌와 동일하게 사용할 수 있습니다.
#Person2#: 죄송합니다, 다시 생각해보겠습니다. B형 계좌는 어떻게 다른가요?
#B형 계좌는 거래에 직접 관여할 수 없고 외부 출금 서비스도 이용할 수 없습니다.
--------------------------------------------------------------

### 첫시작에 #이 없는 경우

In [34]:
idx_list3, _ = findall_pattern(dev_df_person, r'(?<!#)\b[A-Za-z가-힣0-9]+\b#')
for idx in idx_list3:
    print(f'\n[{idx}]')
    print('----'*20)
    print(dev_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list3))

0


### 양쪽에 #이 없는 경우

In [35]:
idx_list4, _ = findall_pattern(dev_df_person, r'(?<!#)\b사람[0-9]+:\s\b') # 사람 Person
for idx in idx_list4:
    print(f'\n[{idx}]')
    print('----'*20)
    print(dev_df_person.iloc[idx, 1])
    print('----'*20)
print(len(idx_list4))

0


### 4가지 경우의 인덱스 값들 중복 제거

In [36]:
person_idx = list(set(idx_list + idx_list2 + idx_list3 + idx_list4))
person_idx = sorted(person_idx)
print(len(person_idx), person_idx)

2 [48, 63]


In [37]:
for idx in person_idx:
    print(f'\n[{idx}]')
    print('----'*20)
    print(dev_df_copy.iloc[idx, 1])
    print('----'*20)


[48]
--------------------------------------------------------------------------------
#Person1#: 무엇을 도와드릴까요?
#Person2#: 네, 다음 주 일요일 전에 출발하는 캐나다 캘거리행 항공편의 좌석 3석을 예약하고 싶습니다.
#Person1#: 이코노미 클래스인가요?
#Person2#: 네.
#Person1#: 편도인가요, 왕복인가요?
#Person2#: 편도입니다.
#Person1#: 직항편이 없습니다. 밴쿠버에서 환승하셔야 합니다.
#Person2#: 괜찮아요.
#다음 주 금요일 오전 10시에 베이징에서 출발하는 캐나다항공 30편이 있습니다. 좌석이 3개 있습니다. 괜찮을까요?
#Person2#: 네, 괜찮습니다.
#Person1#: 성함을 말씀해 주세요.
#Person2#: 바질, 바질입니다. 티켓이 얼마인가요?
#Person1#: 한 장당 580달러입니다.
--------------------------------------------------------------------------------

[63]
--------------------------------------------------------------------------------
#Person1#: 좋아요, 이제 초기 입금에 대해 계속 이야기해 보겠습니다.
#Person2#: 좋은 생각입니다. 얼마를 예치해야 하나요?
#Person1#: 계약 저축의 경우 100, 000위안이 필요합니다.
#Person2#: 필요한 경우 인출은 어떻게 하나요?
#Person1#: 계약 저축 계좌는 결제 계좌와 동일하게 사용할 수 있습니다.
#Person2#: 죄송합니다, 다시 생각해보겠습니다. B형 계좌는 어떻게 다른가요?
#B형 계좌는 거래에 직접 관여할 수 없고 외부 출금 서비스도 이용할 수 없습니다.
--------------------------------------------------------------

In [38]:
print(
    re.sub(r'#B형', '#Person1#: B형', dev_df_copy.iloc[63, 1])
)

#Person1#: 좋아요, 이제 초기 입금에 대해 계속 이야기해 보겠습니다.
#Person2#: 좋은 생각입니다. 얼마를 예치해야 하나요?
#Person1#: 계약 저축의 경우 100, 000위안이 필요합니다.
#Person2#: 필요한 경우 인출은 어떻게 하나요?
#Person1#: 계약 저축 계좌는 결제 계좌와 동일하게 사용할 수 있습니다.
#Person2#: 죄송합니다, 다시 생각해보겠습니다. B형 계좌는 어떻게 다른가요?
#Person1#: B형 계좌는 거래에 직접 관여할 수 없고 외부 출금 서비스도 이용할 수 없습니다.


In [39]:
dev_df_copy.iloc[48, 1] = re.sub(r'#다음', '#Person1#: 다음', dev_df_copy.iloc[48, 1])
dev_df_copy.iloc[63, 1] = re.sub(r'#B형', '#Person1#: B형', dev_df_copy.iloc[63, 1])

In [40]:
dev_df_person.iloc[48, 1] = re.sub(r'#다음', '#Person1#: 다음', dev_df_person.iloc[48, 1])
dev_df_person.iloc[63, 1] = re.sub(r'#B형', '#Person1#: B형', dev_df_person.iloc[63, 1])

idx_list, _ = findall_pattern(dev_df_person, r'#[가-힣]+')
idx_list2, _ = findall_pattern(dev_df_person, r'#\b[A-Za-z가-힣]+\b')
idx_list3, _ = findall_pattern(dev_df_person, r'(?<!#)\b[A-Za-z가-힣0-9]+\b#')
idx_list4, _ = findall_pattern(dev_df_person, r'(?<!#)\b사람[0-9]+:\s\b') # 사람 Person

person_idx = list(set(idx_list + idx_list2 + idx_list3 + idx_list4))
person_idx = sorted(person_idx)
print(len(person_idx), person_idx)

0 []


### 화자가 연속되는 경우

In [41]:
def reg_masking(pattern, text):
    masked = re.findall(pattern, text)
    return masked

In [42]:
masked_train = dev_df_copy['dialogue'].apply(lambda x: str(reg_masking(r'#\bPerson[0-9]+\b#', x)))
for idx in range(0, dev_df_copy.shape[0]):
    print(masked_train[idx])

['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Pe

In [43]:
def repeat_person(word_list):
    for i in range(len(word_list) - 1):
        if word_list[i] == word_list[i+1]:
            return True
    return False

In [44]:
masked_train = masked_train.reset_index()
dev_df_repeat = masked_train['dialogue'].apply(lambda x: x.lstrip('[').rstrip(']').replace("', '", ' ').strip("'").split())

In [45]:
idx_repeat = []
for idx in range(0, dev_df_copy.shape[0]):
    if repeat_person(dev_df_repeat[idx]) == True:
        idx_repeat.append(idx)
print(len(idx_repeat), idx_repeat)

1 [437]


In [46]:
for idx in idx_repeat:
    print(f'\n[{idx}]')
    print('-----'*20)
    print(dev_df_copy.iloc[idx, 1])
    # print(f'>>> {train_df_copy.iloc[idx, 2]}')
    print('-----'*20)


[437]
----------------------------------------------------------------------------------------------------
#Person1#: 리브! 요즘 어떻게 지내?
#Person2#: 안녕! 나는 새로 입양한 고양이와 함께 바쁘게 지내고 있어. 그녀의 사진을 보여줄까?
#Person2#: 뭐? 고양이를 키우고 있었어! 사진 좀 보여줘!
#Person1#: 봐, 그녀는 겨우 3개월이야.
#Person2#: 그래, 알겠어. 얼마나 작은지 봐. 정말 귀여워.
----------------------------------------------------------------------------------------------------


In [47]:
temp = re.sub(r'#Person2#: 뭐', r'#Person1#: 뭐', dev_df_copy.iloc[437, 1])
temp = re.sub(r'#Person1#: 봐', r'#Person2#: 봐', temp)
temp = re.sub(r'#Person2#: 그래', r'#Person1#: 그래', temp)
print(temp)

#Person1#: 리브! 요즘 어떻게 지내?
#Person2#: 안녕! 나는 새로 입양한 고양이와 함께 바쁘게 지내고 있어. 그녀의 사진을 보여줄까?
#Person1#: 뭐? 고양이를 키우고 있었어! 사진 좀 보여줘!
#Person2#: 봐, 그녀는 겨우 3개월이야.
#Person1#: 그래, 알겠어. 얼마나 작은지 봐. 정말 귀여워.


In [48]:
temp = re.sub(r'#Person2#: 뭐', r'#Person1#: 뭐', dev_df_copy.iloc[437, 1])
temp = re.sub(r'#Person1#: 봐', r'#Person2#: 봐', temp)
dev_df_copy.iloc[437, 1] = re.sub(r'#Person2#: 그래', r'#Person1#: 그래', temp)

In [49]:
masked_train = dev_df_copy['dialogue'].apply(lambda x: str(reg_masking(r'#\bPerson[0-9]+\b#', x)))
for idx in range(0, dev_df_copy.shape[0]):
    print(masked_train[idx])

['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#']
['#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Person1#', '#Person2#', '#Pe

In [50]:
masked_train = masked_train.reset_index()
dev_df_repeat = masked_train['dialogue'].apply(lambda x: x.lstrip('[').rstrip(']').replace("', '", ' ').strip("'").split())

In [51]:
idx_repeat = []
for idx in range(0, dev_df_copy.shape[0]):
    if repeat_person(dev_df_repeat[idx]) == True:
        idx_repeat.append(idx)
print(len(idx_repeat), idx_repeat)

0 []


# special token 재확인

In [52]:
def reg_masking(text):
    pattern = r'#\w+#'
    masked = re.findall(pattern, text)
    return masked

masked = train_df_copy['dialogue'].apply(lambda x: str(set(reg_masking(x)))) # dev_df_copy
for idx in range(0, train_df_copy.shape[0]): # dev_df_copy
    print(masked[idx])

{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{'#Person2#', '#Person1#'}
{

In [54]:
temp_df = masked.reset_index()
temp_df['dialogue'] = temp_df['dialogue'].apply(lambda x: set(eval(x)))
unique_dialogues = set().union(*temp_df['dialogue'])
print(sorted(unique_dialogues))

['#Address#', '#CarNumber#', '#CardNumber#', '#DateOfBirth#', '#Email#', '#PassportNumber#', '#Person1#', '#Person2#', '#Person3#', '#Person4#', '#Person5#', '#Person6#', '#Person7#', '#PhoneNumber#', '#SSN#']


# Basic Preprocessing

In [55]:
# 좌우 공백 제거
train_df_copy['dialogue'] = train_df_copy['dialogue'].apply(lambda x: x.strip())
train_df_copy['summary'] = train_df_copy['summary'].apply(lambda x: x.strip())
train_df_copy['topic'] = train_df_copy['topic'].apply(lambda x: x.strip())

# 자음, 모음만으로 구성된 경우 적절한 값으로 대체
train_df_copy['dialogue'] = train_df_copy['dialogue'].apply(lambda x: x.replace('제ㅏ', '제가'))
train_df_copy['dialogue'] = train_df_copy['dialogue'].apply(lambda x: x.replace('척했ㄷ거든', '척했거든'))
train_df_copy['dialogue'] = train_df_copy['dialogue'].apply(lambda x: x.replace('배경ㅇ로', '배경으로'))
train_df_copy['dialogue'] = train_df_copy['dialogue'].apply(lambda x: x.replace('ㅋㅋ', '웃기다'))
train_df_copy['dialogue'] = train_df_copy['dialogue'].apply(lambda x: x.replace('아직ㅍ알맞는', '아직 알맞는'))
train_df_copy['summary'] = train_df_copy['summary'].apply(lambda x: x.replace('머라이어 ㅐ리', '머라이어 캐리'))

# 좌우 공백 제거
dev_df_copy['dialogue'] = dev_df_copy['dialogue'].apply(lambda x: x.strip())
dev_df_copy['summary'] = dev_df_copy['summary'].apply(lambda x: x.strip())
dev_df_copy['topic'] = dev_df_copy['topic'].apply(lambda x: x.strip())

In [56]:
train_df_copy.to_csv('../../data/train_regular-expression.csv', index=False)
dev_df_copy.to_csv('../../data/dev_regular-expression.csv', index=False)